# Topic modelling med gensim og dhlab

In [1]:
import dhlab as dh
import pandas as pd
import gensim
import pyLDAvis
from pprint import pprint
import pyLDAvis.gensim_models as genvis

In [2]:
# sprit urn URN:NBN:no-nb_digibok_2020090207537

Finn en bok

In [3]:
bok = dh.Corpus(doctype="digibok", limit=1, title="Norgeshistorie")

In [4]:
bok

dhlabid                                  urn  \
0  100441759  URN:NBN:no-nb_digibok_2009111200018   

                                               title  \
0  Elevens ressursbok : verdens- og Norgeshistori...   

                                          authors  \
0  Berger , Finn / Henningsen , Rune / Aass , Ole   

                                 oaiid                           sesamid  \
0  oai:nb.bibsys.no:999721559964702202  9d569a267470cda9851b718c9bdd20f0   

       isbn10 city  timestamp  year          publisher langs  \
0  8200423387        19970101  1997  Universitetsforl.   nob   

                                            subjects ddc genres  \
0  Eldre tid / Tidlig nytid / Historie / Verden /...              

    literaryform  doctype ocr_creator  ocr_timestamp  
0  Faglitteratur  digibok          nb       20060101

In [5]:
urn = bok.frame.urn.tolist()[0]
urn

'URN:NBN:no-nb_digibok_2009111200018'

## Chunking

In [6]:
# Chunks 
res = dh.Chunks(chunks=1000, urn=urn)

In [7]:
len(res.chunks)

31

In [8]:
def chunks_to_corpus(chunks_list):
    res = []
    for x in chunks_list:
        inner_res = ""
        for y in x:
            inner_res += (y + " ") * x[y]
            
        res.append(inner_res)
    return res

In [9]:
texts = chunks_to_corpus(res.chunks)

## Find delta TFIDF

In [10]:
df = pd.DataFrame(res.chunks).transpose().fillna(0)

In [11]:
df

0     1     2     3     4     5     6     7     8     9   ...  \
(           8.0   0.0   4.0   1.0   4.0   4.0   2.0   4.0  11.0   4.0  ...   
)           8.0   0.0   4.0   1.0   4.0   4.0   2.0   4.0  11.0   4.0  ...   
,          49.0  36.0  44.0  60.0  43.0  39.0  55.0  42.0  20.0  55.0  ...   
-           8.0   5.0   2.0   5.0   4.0   3.0   3.0   8.0   3.0   6.0  ...   
.          22.0  38.0  25.0  27.0  25.0  25.0  37.0  24.0  32.0  36.0  ...   
...         ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
verdighet   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
virkelige   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
Ørkenen     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
årer        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
ødela       0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   

             21    22    23    24    25    26    27    28    29    30  
(           2.0   3.0   2.0   6.0   4.0   1.0   5.0   3.0   2.0   1.0  
)           2.0   3.0   2.0   5.0   5.0   1.0   5.0   3.0   2.0   1.0  
,          38.0  39.0  40.0  45.0  58.0  38.0  32.0  41.0  42.0  38.0  
-           4.0  10.0   9.0   1.0   2.0   1.0   5.0  20.0   3.0   0.0  
.          27.0  46.0  32.0  41.0  17.0  38.0  36.0  31.0  41.0  40.0  
...         ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
verdighet   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0  
virkelige   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0  
Ørkenen     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0  
årer        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0  
ødela       0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   1.0  

[6844 rows x 31 columns]

In [12]:
# Import top 50000 tokens from NB collection
tot = dh.totals(50000)

In [13]:
# Divide corpus freq count by tot
res = df.sum(axis=1) /  tot.freq

In [14]:
# Get top 1000 more frequent tokens
target_tokens = res.sort_values(ascending=False).iloc[:1000].dropna().index

In [15]:
df.loc[target_tokens]

0    1    2    3    4    5    6    7    8    9   ...   21   22  \
Forstå     0.0  3.0  3.0  0.0  2.0  0.0  0.0  0.0  0.0  6.0  ...  3.0  3.0   
FØR        3.0  2.0  3.0  3.0  4.0  2.0  2.0  2.0  2.0  3.0  ...  4.0  2.0   
vikingene  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
læreboka   0.0  0.0  1.0  0.0  1.0  1.0  1.0  0.0  1.0  0.0  ...  2.0  0.0   
1850       4.0  2.0  3.0  3.0  4.0  2.0  2.0  2.0  2.0  3.0  ...  4.0  4.0   
...        ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
fortrinn   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
hustruen   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  ...  0.0  0.0   
liga       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
skitt      0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
van-       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   

            23   24   25   26   27   28   29   30  
Forstå     1.0  0.0  1.0  4.0  0.0  1.0  0.0  0.0  
FØR        2.0  2.0  3.0  3.0  1.0  3.0  1.0  1.0  
vikingene  0.0  2.0  0.0  0.0  0.0  0.0  0.0  0.0  
læreboka   0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  
1850       2.0  2.0  3.0  3.0  1.0  4.0  1.0  1.0  
...        ...  ...  ...  ...  ...  ...  ...  ...  
fortrinn   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
hustruen   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
liga       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
skitt      1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
van-       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[1000 rows x 31 columns]

In [16]:
outer_lst = []

for col in df.loc[target_tokens].columns:
    inner_str = ""
    for i, x in df.loc[target_tokens][col].items():
        if x > 0:
            inner_str += (i + " ") * int(x)
        
    outer_lst.append(inner_str)


In [17]:
len(outer_lst)

31

## Prep for LDA

In [18]:
data = [x.split() for x in outer_lst]

In [19]:
id2word = gensim.corpora.Dictionary(data)

In [20]:
corpus = [id2word.doc2bow(chunk) for chunk in data]

## Make model

In [21]:
lda_model = gensim.models.LdaMulticore(
    corpus = corpus,
    id2word = id2word,
    num_topics = 10
)

In [22]:
pprint(lda_model.print_topics())

[(0,
  '0.022*"brenning" + 0.015*"1650" + 0.014*"faget" + 0.014*"1850" + '
  '0.014*"Hva" + 0.014*"FØR" + 0.011*"målene" + 0.011*"EUROPA" + 0.010*"NYE" + '
  '0.010*"hersker"'),
 (1,
  '0.022*"Hva" + 0.017*"1850" + 0.013*"garden" + 0.012*"Kilde" + '
  '0.011*"revolusjon" + 0.011*"sådde" + 0.010*"slags" + 0.009*"industrielle" + '
  '0.009*"skipet" + 0.008*"FØR"'),
 (2,
  '0.020*"1850" + 0.015*"Hva" + 0.015*"FØR" + 0.014*"garden" + '
  '0.012*"Kapittel" + 0.011*"Kilde" + 0.010*"sådde" + 0.009*"Forstå" + '
  '0.009*"slags" + 0.008*"1814"'),
 (3,
  '0.013*"faget" + 0.009*"målene" + 0.007*"Vurdering" + 0.006*"kjennskap" + '
  '0.006*"menneskene" + 0.006*"middels" + 0.005*"Lag" + 0.005*"læreplanen" + '
  '0.005*"læreren" + 0.005*"informere"'),
 (4,
  '0.032*"Hva" + 0.025*"Hvordan" + 0.023*"1850" + 0.020*"FØR" + '
  '0.016*"Oppgave" + 0.016*"Forstå" + 0.015*"Spørsmål" + 0.014*"slags" + '
  '0.010*"Hvilke" + 0.010*"perioden"'),
 (5,
  '0.031*"Hva" + 0.014*"1850" + 0.014*"slags" + 0.014*"Hvorda

In [23]:
prep = genvis.prepare(lda_model, corpus, id2word)

In [24]:
# Save to html
# pyLDAvis.save_html(prep, "result.html")

In [25]:
pyLDAvis.enable_notebook()

In [26]:
pyLDAvis.display(prep)